In [0]:
%run ../_utils


# Camada bronze

Na camada bronze, nenhuma limpeza ou regra de negócio devem ser aplicadas aos dados.

só vamos ler em parquet e salvar em delta.

Vamos também utilizar da tabela de controle para termos o milestone da ultima execução (aqui nao será utilizado de fato, mas é interessante justamenete para o UPSERT)

## 1 - Processamento da camada bronze

Aqui vamos adicionar uma estrutura que permite um laço de repetição.

O laço será responsável por armazenar os dados e criar tabela delta para cada "entidade" definida no diagrama ER

In [0]:
data = {
    "table_name": [
        "customers",
        "orders",
        "geolocation",
        "products",
        "order_items",
        "sellers",
        "order_payments",
        "product_category_name_translation",
        "order_reviews",
    ],
    "dataset_location": [
        "olist_customers_dataset",
        "olist_orders_dataset",
        "olist_geolocation_dataset",
        "olist_products_dataset",
        "olist_order_items_dataset",
        "olist_sellers_dataset",
        "olist_order_payments_dataset",
        "product_category_name_translation",
        "olist_order_reviews_dataset",
    ],
}


bronze_tables = list(zip(data["table_name"], data["dataset_location"]))


## 2 - Persistência

Estamos pegando os arquivos em parquet (passo apenas didático), salvando os dados em delta e criando as tabelas delta

In [0]:
for table_name, dataset_location in bronze_tables:
    # read data
    parquet_location = f"/FileStore/parquet/brazilian_ecommerce/{dataset_location}"
    target_location = f"dbfs:/delta/brazilian_ecommerce/{dataset_location}/bronze"

    df = spark.read.parquet(parquet_location)
    tb_name = f"olist_bronze.{table_name}"

    save_dataframe(df, format_mode="delta", table_name=tb_name, target_location=target_location)

    create_table(table_name=tb_name, target_location=target_location)
    
    print()

[LOG] Saving olist_bronze.customers delta on dbfs:/delta/brazilian_ecommerce/olist_customers_dataset/bronze... OK!
[LOG] Creating delta table olist_bronze.customers on dbfs:/delta/brazilian_ecommerce/olist_customers_dataset/bronze... OK!

[LOG] Saving olist_bronze.orders delta on dbfs:/delta/brazilian_ecommerce/olist_orders_dataset/bronze... OK!
[LOG] Creating delta table olist_bronze.orders on dbfs:/delta/brazilian_ecommerce/olist_orders_dataset/bronze... OK!

[LOG] Saving olist_bronze.geolocation delta on dbfs:/delta/brazilian_ecommerce/olist_geolocation_dataset/bronze... OK!
[LOG] Creating delta table olist_bronze.geolocation on dbfs:/delta/brazilian_ecommerce/olist_geolocation_dataset/bronze... OK!

[LOG] Saving olist_bronze.products delta on dbfs:/delta/brazilian_ecommerce/olist_products_dataset/bronze... OK!
[LOG] Creating delta table olist_bronze.products on dbfs:/delta/brazilian_ecommerce/olist_products_dataset/bronze... OK!

[LOG] Saving olist_bronze.order_items delta on dbfs:

In [0]:
dbutils.notebook.exit("OK")

In [0]:
%sql

select count(*) from olist_bronze.order_items

count(1) 112650

In [0]:
%sql

select * from olist_bronze.order_items

order_id order_item_id product_id seller_id shipping_limit_date price freight_value 00010242fe8c5a6d1ba2dd792cb16214 1 4244733e06e7ecb4970a6e2683c13e61 48436dade18ac8b2bce089ec2a041202 2017-09-19T09:45:35Z 58.9 13.29 00018f77f2f0320c557190d7a144bdd3 1 e5f2d52b802189ee658865ca93d83a8f dd7ddc04e1b6c2c614352b383efe2d36 2017-05-03T11:05:13Z 239.9 19.93 000229ec398224ef6ca0657da4fc703e 1 c777355d18b72b67abbeef9df44fd0fd 5b51032eddd242adc84c38acab88f23d 2018-01-18T14:48:30Z 199.0 17.87 00024acbcdf0a6daa1e931b038114c75 1 7634da152a4610f1595efa32f14722fc 9d7a1d34a5052409006425275ba1c2b4 2018-08-15T10:10:18Z 12.99 12.79 00042b26cf59d7ce69dfabb4e55b4fd9 1 ac6c3623068f30de03045865e4e10089 df560393f3a51e74553ab94004ba5c87 2017-02-13T13:57:51Z 199.9 18.14 00048cc3ae777c65dbb7d2a0634bc1ea 1 ef92defde845ab8450f9d70c526ef70f 6426d21aca402a131fc0a5d0960a3c90 2017-05-23T03:55:27Z 21.9 12.69 00054e8431b9d7675808bcb819fb4a32 1 8d4f2bb7e93e6710a28f34fa83ee7d28 7040e82f899a04d1b434b795a43b4617 2017-12-14T12:10:31Z 19.9 11.85 000576fe39319847cbb9d288c5617fa6 1 557d850972a7d6f792fd18ae1400d9b6 5996cddab893a4652a15592fb58ab8db 2018-07-10T12:30:45Z 810.0 70.75 0005a1a1728c9d785b8e2b08b904576c 1 310ae3c140ff94b03219ad0adc3c778f a416b6a846a11724393025641d4edd5e 2018-03-26T18:31:29Z 145.95 11.65 0005f50442cb953dcd1d21e1fb923495 1 4535b0e1091c278dfd193e5a1d63b39f ba143b05f0110f0dc71ad71b4466ce92 2018-07-06T14:10:56Z 53.99 11.4 00061f2a7bc09da83e415a52dc8a4af1 1 d63c1011f49d98b976c352955b1c4bea cc419e0650a3c5ba77189a1882b7556a 2018-03-29T22:28:09Z 59.99 8.88 00063b381e2406b52ad429470734ebd5 1 f177554ea93259a5b282f24e33f65ab6 8602a61d680a10a82cceeeda0d99ea3d 2018-07-31T17:30:39Z 45.0 12.98 0006ec9db01a64e59a68b2c340bf65a7 1 99a4788cb24856965c36a24e339b6058 4a3ca9315b744ce9f8e9374361493884 2018-07-26T17:24:20Z 74.0 23.32 0008288aa423d2a3f00fcb17cd7d8719 1 368c6c730842d78016ad823897a372db 1f50f920176fa81dab994f9023523100 2018-02-21T02:55:52Z 49.9 13.37 0008288aa423d2a3f00fcb17cd7d8719 2 368c6c730842d78016ad823897a372db 1f50f920176fa81dab994f9023523100 2018-02-21T02:55:52Z 49.9 13.37 0009792311464db532ff765bf7b182ae 1 8cab8abac59158715e0d70a36c807415 530ec6109d11eaaf87999465c6afee01 2018-08-17T12:15:10Z 99.9 27.65 0009c9a17f916a706d71784483a5d643 1 3f27ac8e699df3d300ec4a5d8c5cf0b2 fcb5ace8bcc92f75707dc0f01a27d269 2018-05-02T09:31:53Z 639.0 11.34 000aed2e25dbad2f9ddb70584c5a2ded 1 4fa33915031a8cde03dd0d3e8fb27f01 fe2032dab1a61af8794248c8196565c9 2018-05-16T20:57:03Z 144.0 8.77 000c3e6612759851cc3cbb4b83257986 1 b50c950aba0dcead2c48032a690ce817 218d46b86c1881d022bce9c68a7d4b15 2017-08-21T03:33:13Z 99.0 13.71 000e562887b1f2006d75e0be9558292e 1 5ed9eaf534f6936b51d0b6c5e4d5c2e9 8cbac7e12637ed9cffa18c7875207478 2018-02-28T12:08:37Z 25.0 16.11 000e63d38ae8c00bbcb5a30573b99628 1 553e0e7590d3116a072507a3635d2877 1c129092bf23f28a5930387c980c0dfc 2018-03-29T20:07:49Z 47.9 8.88 000e906b789b55f64edcb1f84030f90d 1 57d79905de06d8897872c551bfd09358 ea8482cd71df3c1969d7b9473ff13abc 2017-11-27T19:09:02Z 21.99 11.85 000f25f4d72195062c040b12dce9a18a 1 1c05e0964302b6cf68ca0d15f326c6ba 7c67e1448b00f6e969d365cea6b010ab 2018-03-21T11:10:11Z 119.99 44.4 001021efaa8636c29475e7734483457d 1 5d7c23067ed3fc8c6e699b9373d5890b 6560211a19b47992c3666cc44a7e94c0 2018-03-05T09:35:41Z 49.0 15.1 0010b2e5201cc5f1ae7e9c6cc8f5bd00 1 5a419dbf24a8c9718fe522b81c69f61a 3504c0cb71d7fa48d967e0e4c94d59d9 2017-09-15T18:04:37Z 48.9 16.6 00119ff934e539cf26f92b9ef0cdfed8 1 21b1c2f67a9aafb5af0eb06c13b9dbda c864036feaab8c1659f65ea4faebe1da 2017-08-11T00:35:12Z 219.9 16.98 0011d82c4b53e22e84023405fb467e57 1 c389f712c4b4510bc997cee93e8b1a28 bfd27a966d91cfaafdb25d076585f0da 2018-01-29T21:51:25Z 289.0 26.33 00125cb692d04887809806618a2a145f 1 1c0c0093a48f13ba70d0c6b0a9157cb7 41b39e28db005d9731d9d485a83b4c38 2017-03-29T13:05:42Z 109.9 25.51 00130c0eee84a3d909e75bc08c5c3ca1 1 89321f94e35fc6d7903d36f74e351d40 16090f2ca825584b5a147ab24aa30c86 2018-06-14T05:16:24Z 27.9 7.94 0013503b13da1eac686219390b7d641b 1 38afdf723b95d45

In [0]:
%sql

select * from olist_bronze.order_reviews

review_id order_id review_score review_comment_title review_comment_message review_creation_date review_answer_timestamp 7bc2406110b926393aa56f80a40eba40 73fc7af87114b39712e6da79b0a377eb 4 null null 2018-01-18T00:00:00Z 2018-01-18T21:46:59Z 80e641a11e56f04c1ad469d5645fdfde a548910a1c6147796b98fdf73dbeba33 5 null null 2018-03-10T00:00:00Z 2018-03-11T03:05:13Z 228ce5500dc1d8e020d8d1322874b6f0 f9e4b658b201a9f2ecdecbb34bed034b 5 null null 2018-02-17T00:00:00Z 2018-02-18T14:36:24Z e64fb393e7b32834bb789ff8bb30750e 658677c97b385a9be170737859d3511b 5 null Recebi bem antes do prazo estipulado. 2017-04-21T00:00:00Z 2017-04-21T22:02:06Z f7c4243c7fe1938f181bec41a392bdeb 8e6bfb81e283fa7e4f11123a3fb894f1 5 null Parabéns lojas lannister adorei comprar pela Internet seguro e prático Parabéns a todos feliz Páscoa 2018-03-01T00:00:00Z 2018-03-02T10:26:53Z 15197aa66ff4d0650b5434f1b46cda19 b18dcdf73be66366873cd26c5724d1dc 1 null null 2018-04-13T00:00:00Z 2018-04-16T00:39:37Z 07f9bee5d1b850860defd761afa7ff16 e48aa0d2dcec3a2e87348811bcfdf22b 5 null null 2017-07-16T00:00:00Z 2017-07-18T19:30:34Z 7c6400515c67679fbee952a7525281ef c31a859e34e3adac22f376954e19b39d 5 null null 2018-08-14T00:00:00Z 2018-08-14T21:36:06Z a3f6f7f6f433de0aefbb97da197c554c 9c214ac970e84273583ab523dfafd09b 5 null null 2017-05-17T00:00:00Z 2017-05-18T12:05:37Z 8670d52e15e00043ae7de4c01cc2fe06 b9bf720beb4ab3728760088589c62129 4 recomendo aparelho eficiente. no site a marca do aparelho esta impresso como 3desinfector e ao chegar esta com outro nome...atualizar com a marca correta uma vez que é o mesmo aparelho 2018-05-22T00:00:00Z 2018-05-23T16:45:47Z c9cfd2d5ab5911836ababae136c3a10c cdf9aa68e72324eeb25c7de974696ee2 5 null null 2017-12-23T00:00:00Z 2017-12-26T14:36:03Z 96052551d87e5f62e6c9f6974ec392e9 3d374c9e46530bb5ed4a7648915306a6 5 null null 2017-12-19T00:00:00Z 2017-12-20T10:25:22Z 4b49719c8a200003f700d3d986ea1a19 9d6f15f95d01e79bd1349cc208361f09 4 null Mas um pouco ,travando...pelo valor ta Boa.
 2018-02-16T00:00:00Z 2018-02-20T10:52:22Z 23f75a37effc35d9a915b4e1ad483793 2eaf8e099d871cd5c22b83b5ea8f6e0e 4 null null 2018-03-28T00:00:00Z 2018-03-30T15:10:55Z 9a0abbb668bafb95a6d2b05db43284c4 d7bd0e4afdf94846eb73642b4e3e75c3 3 null null 2017-04-30T00:00:00Z 2017-05-03T00:02:22Z 3948b09f7c818e2d86c9a546758b2335 e51478e7e277a83743b6f9991dbfa3fb 5 Super recomendo Vendedor confiável, produto ok e entrega antes do prazo. 2018-05-23T00:00:00Z 2018-05-24T03:00:01Z 9314d6f9799f5bfba510cc7bcd468c01 0dacf04c5ad59fd5a0cc1faa07c34e39 2 null GOSTARIA DE SABER O QUE HOUVE, SEMPRE RECEBI E ESSA COMPRA AGORA ME DECPCIONOU 2018-01-18T00:00:00Z 2018-01-20T21:25:45Z 8e15a274d95600fa14f8be64e37a0e67 ff1581e08b3011021e7c7de592ddc81e 5 null null 2018-03-24T00:00:00Z 2018-03-26T15:58:32Z fdbdb2629a7cde0f66657acc92084e7f 70a752414a13d09cc1f2b437b914b28e 3 null null 2017-09-29T00:00:00Z 2017-10-02T01:12:49Z 373cbeecea8286a2b66c97b1b157ec46 583174fbe37d3d5f0d6661be3aad1786 1 Não chegou meu produto Péssimo 2018-08-15T00:00:00Z 2018-08-15T04:10:37Z a2ff510ca4e059c3fefc7a7866571f6f a9953b2f0b1665ac7586cc5a6ac8f58c 4 null null 2017-10-06T00:00:00Z 2017-10-08T22:36:05Z 80c70bc263881ba6525f6cee1d94ac87 ae168dfba236919411fe08f336fefa44 5 null null 2018-03-17T00:00:00Z 2018-04-04T19:41:11Z d21bbc789670eab777d27372ab9094cc 4fc44d78867142c627497b60a7e0228a 5 Ótimo Loja nota 10 2018-07-10T00:00:00Z 2018-07-11T14:10:25Z 7bcb3c758c67f23638262c731493e848 7c9956750739a47dba7a6928ba2f0245 5 null null 2017-09-09T00:00:00Z 2017-10-17T02:25:47Z 0e0190b9db53b689b285d3f3916f8441 79832b7cb59ac6f887088ffd686e1d5e 5 null obrigado pela atençao amim dispensada 2017-12-01T00:00:00Z 2017-12-09T22:58:58Z 66e4430c5bc6b7e3773886bf1c14d912 84cec4f65c7a4f2f54c294a30224a594 5 null null 2017-06-23T00:00:00Z 2017-06-27T00:52:02Z bf566b3910c328733baf7fca7d2be041 a59a15e4b6085c752d338431dc68d464 4 null null 2017-11-01T00:00:00Z 2017-11-01T20:25:30Z fe3db7c069d694bab50cc43463f91608 2ca73e2ff9e3a186ad1e1ffb9b1d9c10 5 null A compra foi realizada

In [0]:
%sql

select * from olist_bronze.sellers

seller_id seller_zip_code_prefix seller_city seller_state 3442f8959a84dea7ee197c632cb2df15 13023 campinas SP d1b65fc7debc3361ea86b5f14c68d2e2 13844 mogi guacu SP ce3ad9de960102d0677a81f5d0bb7b2d 20031 rio de janeiro RJ c0f3eea2e14555b6faeea3dd58c1b1c3 4195 sao paulo SP 51a04a8a6bdcb23deccc82b0b80742cf 12914 braganca paulista SP c240c4061717ac1806ae6ee72be3533b 20920 rio de janeiro RJ e49c26c3edfa46d227d5121a6b6e4d37 55325 brejao PE 1b938a7ec6ac5061a66a3766e0e75f90 16304 penapolis SP 768a86e36ad6aae3d03ee3c6433d61df 1529 sao paulo SP ccc4bbb5f32a6ab2b7066a4130f114e3 80310 curitiba PR 8cb7c5ddf41f4d506eba76e9a4702a25 75110 anapolis GO a7a9b880c49781da66651ccf4ba9ac38 13530 itirapina SP 8bd0f31cf0a614c658f6763bd02dea69 1222 sao paulo SP 05a48cc8859962767935ab9087417fbb 5372 sao paulo SP 7b8e8ec35bad4b0ef7e3963650b0a87b 88705 tubarao SC 1444c08e64d55fb3c25f0f09c07ffcf2 42738 lauro de freitas BA 166e8f1381e09651983c38b1f6f91c11 88780 imbituba SC e38db885400cd35c71dfd162f2c1dbcf 70740 brasilia DF d2e753bb80b7d4faa77483ed00edc8ca 45810 porto seguro BA f9ec7093df3a7b346b7bcf7864069ca3 5138 sao paulo SP 4e6015589b781adaa5ce7f1892d06bb1 11440 guaruja SP 4cf490a58259286ada5ba8525ba9e84a 14910 tabatinga SP f7496d659ca9fdaf323c0aae84176632 4156 sao paulo SP 2ff97219cb8622eaf3cd89b7d9c09824 13320 salto SP 8bd0e3abda539b9479c4b44a691be1ec 98910 tres de maio RS 2a1348e9addc1af5aaa619b1a3679d6b 30494 belo horizonte MG 2078fe5066350e7d220c0ad3a3bbc6c1 86707 arapongas PR 116ccb1a1604bc88e4d234a8c23f33de 9850 sao bernardo do campo SP 430315b7bb4b6e4b3c978f9dfa9b0558 4857 sao paulo SP 406822777a0b9eb5c50e442dd4cd3ec5 18500 tatui SP 4dbd95a08b31ede5c82d3f861cb1ce1a 80210 curitiba PR e9e446d01bd10a97a8ffcfc4a3a20cb2 2261 sao paulo SP d52cbce9845184537284a23c3bc3da0e 88495 garopaba SC d9a84e1403de8da0c3aa531d6d108ba6 3562 sao paulo SP 9c690ceacd5c66731bf443ea810195cb 37650 camanducaia MG 1f9ab4708f3056ede07124aad39a2554 17602 tupa SP 1961c3e1272bfeceb05d0b78b5bbfdaf 7241 guarulhos SP d3e7d37c0df9aef383f3f2a15b0dddfb 83050 sao jose dos pinhais PR ec2e006556300a79a5a91e4876ab3a56 3445 sao paulo SP b2a6d334e2833acea353624840e25a0e 4133 sao paulo SP d3674f271c91f824f82d24d92011f669 72233 brasilia DF 768de2a4fc06aacecb9a586ccc30746a 70645 brasilia DF a81466620e46a6970b22ef40379fdfc9 88730 sao ludgero SC 5c030029b5916fed0986310385ec9009 88075 sao jose SC c0f783394e37cd9c9d7f5f81141450fa 13416 piracicaba SP c353f8fc0ce8344999f17d578eb69a5e 90850 porto alegre RS 8444e55c1f13cd5c179851e5ca5ebd00 37584 congonhal MG 28a26ebce31d5918b181ede016fd693b 31950 belo horizonte MG 41ab63a91b8b264e8c8780368bf1dd5b 31555 belo horizonte MG 8759e7aedd644f487315e5860962f162 9251 santo andre SP e546117ed9cafbc40239c0c78635c584 4705 sao paulo SP d71d863e5ef30d94e440c11be17dcd8f 6144 osasco SP 0c7533c71df861ec58ad7ff999ed0e8d 13270 valinhos SP ef990a83bbea832f36ebe81376335aa8 89214 joinville SC 41e0fa5761c886a630994a55c12087e7 11446 guaruja SP 0747d5bb69f0586cc869d8af4c50f93e 28990 saquarema RJ 7d294cf9a6a69dc6a0c3e540fff0e039 88390 barra velha SC c89cf7c468a48af70aada384e722f9e2 25730 petropolis RJ b7ba853e9551f4558440881fd3e5c815 95500 santo antonio da patrulha RS 13c2ed7698b3ca92dad49e849219da59 84010 ponta grossa PR cbbd5ae8f53de5f5097cd8217b529e24 6544 santana de parnaiba SP 02ecc2a19303f05e59ce133fd923fff7 9121 santo andre SP c013e57c075a06e5b5c48ee03c525719 13568 sao carlos SP 55f7a3319d80f7fdf078b8f03e6725fe 6056 osasco SP 2d50d6282f8aa2257819a77bfaa0efe0 14940 ibitinga SP b7e1750c1157341d2abd0251e07c186b 5741 sao paulo SP b90e891671cffd9557f33a97dc523645 83010 sao jose dos pinhais PR a416b6a846a11724393025641d4edd5e 3702 sao paulo SP 7e93a43ef30c4f03f38b393420bc753a 6429 barueri SP 5206cc4bc2297c833e6061c49bf9c43f 6192 osasco SP f410c8873029fcc3809b9df6d0b28914 95076 caxias do sul SP ef506c96320abeedfb894c34db06f478 3569 sao paulo SP a13aaf2d2886ab9fb30fb9a920160b8f 89207 joinville SC 7299e27ed73d2ad986de7f7c77d919fa 38440 araguari MG 8a9260f2b0340411d6d2a56bcf4f7378 3